In [5]:
import lightgbm as lgbm
import numpy as  np
import pandas  as pd 
import plotly.graph_objects as go
import yaml 

from aequitas.group import Group
from sklearn.preprocessing import LabelEncoder
from sklearn import metrics 
from random_search import RandomValueTrial, suggest_callable_hyperparams

In [6]:
# lets get the hyperparpmeter
with open ("lightgbm_hyperparameter_tuneing.yaml", "r") as file :
    hyper_parameter = yaml.load(file, Loader=yaml.FullLoader)

In [7]:
hyper_parameter

{'LightGBM': {'classpath': 'Lightgbm.LGBMClassifier',
  'kwargs': {'n_estimators': {'type': 'int',
    'range': [20, 10000],
    'log': True},
   'max_depth': {'type': 'int', 'range': [3, 30]},
   'learning_rate': {'type': 'float', 'range': [0.02, 0.1], 'log': True},
   'num_leaves': {'type': 'int', 'range': [10, 100], 'log': True},
   'bososting_type': ['gdbt', 'goss'],
   'min_data_in_leaf': {'type': 'int', 'range': [5, 200], 'log': True},
   'max_bin': {'type': 'int', 'range': [100, 500]},
   'enable_bindle': [True, False]}}}

In [8]:
trail = RandomValueTrial(seed=1)
suggest_callable_hyperparams(trail,hyper_parameter)

{'classpath': 'Lightgbm.LGBMClassifier',
 'n_estimators': 263,
 'max_depth': 23,
 'learning_rate': 0.020003681922217444,
 'num_leaves': 19,
 'bososting_type': 'gdbt',
 'min_data_in_leaf': 9,
 'max_bin': 238,
 'enable_bindle': False}

In [13]:
# Path to datasets.
base_path = r"C://works//learnings//time_series//data//baf_processed//"

datasets_paths = {
    "Base":    base_path + "Base.parquet",
    "TypeI":   base_path + "Variant I.parquet",
    "TypeII":  base_path + "Variant II.parquet",
    "TypeIII": base_path + "Variant III.parquet",
    "TypeIV":  base_path + "Variant IV.parquet",
    "TypeV":   base_path + "Variant V.parquet",
    
}

In [14]:
# Lets read the dataset one by one 
datasets = { key:pd.read_parquet(path) for key, path in datasets_paths.items()}

In [16]:
print(datasets)

{'Base':         fraud_bool  income  ...  device_fraud_count  month
0                0     0.3  ...                   0      0
1                0     0.8  ...                   0      0
2                0     0.8  ...                   0      0
3                0     0.6  ...                   0      0
4                0     0.9  ...                   0      0
...            ...     ...  ...                 ...    ...
999995           0     0.8  ...                   0      7
999996           0     0.9  ...                   0      7
999997           0     0.8  ...                   0      7
999998           0     0.9  ...                   0      7
999999           0     0.6  ...                   0      7

[1000000 rows x 32 columns], 'TypeI':         fraud_bool  income  ...  device_fraud_count  month
0                0     0.9  ...                   0      0
1                0     0.4  ...                   0      0
2                0     0.7  ...                   0      0
3       

In [19]:
label = "fraud_bool"

categorical_features = [
    "payment_type",
    "employment_status",
    "housing_status",
    "source",
    "device_os",
]

In [18]:
# Create the train and test sets. Shuffle data with `sample` method.
# The split was done by month. The first 6 months as the train, the last 2 months as test.
train_dfs = {key: df[df["month"]<6].sample(frac=1, replace=False) for key, df in datasets.items()}
test_dfs = {key: df[df["month"]>=6].sample(frac=1, replace=False) for key, df in datasets.items()}

In [20]:
# Encode the categorical variables in the datasets to integers. 
# This is expected by LGBM (or columns with the `categorical` data type).

for name in datasets.keys():  # For each dataset in the suite
    train = train_dfs[name]
    test = test_dfs[name]

    for feat in categorical_features:
        encoder = LabelEncoder()
        encoder.fit(train[feat])  # Fit an encoder to the train set.
        train[feat] = encoder.transform(train[feat])  # Transform train set.
        test[feat] = encoder.transform(test[feat])    # Transform test set.

In [23]:
# Cell with train loop.

# Define number of trials in Random search.
n_trials=100
# Random state for sampling seeds.
np.random.seed(42)
# Seeds for the random search sampling algorithm.
seeds = np.random.choice(list(range(1_000_000)), size=n_trials, replace=False)

# Variable to store the results.
runs = {}

for trial in range(n_trials):
    seed = seeds[trial]
    trial = RandomValueTrial(seed=seed)
    # Hyperparameters for the random search trial.
    test_hyperparams = suggest_callable_hyperparams(trial, hyper_parameter)
    del test_hyperparams["classpath"] # Remove unnecessary key in hyperparaemters.
    
    # Update list of tested hyperparameters.
    prev_hyperparams = runs.get("hyperparams", [])
    prev_hyperparams.append(test_hyperparams)
    runs["hyperparams"] = prev_hyperparams
    
    for dataset_name in datasets.keys():  # Run hyperparameters on all variants of datastes.
        model = lgbm.LGBMClassifier(n_jobs=10, **test_hyperparams)  # Instantiate LGBM Model.
        X_train = train_dfs[dataset_name].drop(columns=["fraud_bool"])
        y_train = train_dfs[dataset_name]["fraud_bool"]
        X_test = test_dfs[dataset_name].drop(columns=["fraud_bool"])
        y_test = test_dfs[dataset_name]["fraud_bool"]
        # find datetime columns (naive and tz-aware)
        dt_cols = list(X_train.select_dtypes(include=['datetime64[ns]']).columns) \
                + list(X_train.select_dtypes(include=['datetimetz']).columns)

        # Option A: convert to epoch seconds (UTC-based for tz-aware)
        for c in dt_cols:
            if str(X_train[c].dtype).startswith('datetime64[ns,'):
                # tz-aware -> nanoseconds since epoch (UTC), then to seconds
                X_train[c] = X_train[c].view('int64') // 10**9
                X_test[c]  = X_test[c].view('int64') // 10**9
            else:
                # naive -> nanoseconds since epoch, then to seconds
                X_train[c] = X_train[c].view('int64') // 10**9
                X_test[c]  = X_test[c].view('int64') // 10**9
        # Fit model to training data.
        model.fit(X_train, y_train, categorical_feature=categorical_features)
        # Obtain predictions in test data.
        predictions = model.predict_proba(X_test)[:, 1]
        
        # Obtain ROC curve for the predictions.
        fprs, tprs, thresholds = metrics.roc_curve(y_test, predictions)
        # Obtain threshold and recall. We select 5% FPR as threshold.
        threshold = np.min(thresholds[fprs==max(fprs[fprs < 0.05])])
        recall = np.max(tprs[fprs==max(fprs[fprs < 0.05])])

        # Binarize predictions for Aequitas.
        preds_binary = (predictions > threshold).astype(int)
        
        # Create a dataframe with protected group column, predictions and labels.
        # Here, we select age>=50 as threshold.
        aequitas_df = pd.DataFrame(
            {
                "age": (X_test["customer_age"]>=50).map({True: "Older", False: "Younger"}),
                "preds": preds_binary,
                "y": y_test.values
            }
        )
        
        # Obtain FPR results for different groups.
        g = Group()
        aequitas_results = g.get_crosstabs(aequitas_df, attr_cols=["age"], score_col="preds", label_col="y")[0]
        
        # Store the results for the trained model
        results = {}
        results["recall"] = recall
        results["recall Older"] = aequitas_results[aequitas_results["attribute_value"] == "Older"][["tpr"]].values[0][0]
        results["recall Younger"] = aequitas_results[aequitas_results["attribute_value"] == "Younger"][["tpr"]].values[0][0]
        results["fpr Older"] = aequitas_results[aequitas_results["attribute_value"] == "Older"][["fpr"]].values[0][0]
        results["fpr Younger"] = aequitas_results[aequitas_results["attribute_value"] == "Younger"][["fpr"]].values[0][0]
        
        # Store the results in the runs variable
        prev_runs = runs.get(dataset_name, [])
        prev_runs.append(results)
        runs[dataset_name] = prev_runs

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:39: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:40: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Info] Number of positive: 8151, number of negative: 786838
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.026614 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2753
[LightGBM] [Info] Number of data points in the train set: 794989, number of used features: 29
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.010253 -> initscore=-4.569882
[LightGBM] [Info] Start training 

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:39: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:40: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=22, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=22
[LightGBM] [Info] Number of positive: 8151, number of negative: 786839
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.022386 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2753
[LightGBM] [Info] Number of data points in the train set: 794990, number of used features: 29
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.010253 -> initscore=-4.569883
[LightGBM] [Info] Start training 

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:39: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:40: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



...

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:39: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:40: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Info] Number of positive: 8151, number of negative: 786839
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.024116 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1733
[LightGBM] [Info] Number of data points in the train set: 794990, number of used features: 29
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.010253 -> initscore=-4.569883
[LightGBM] [Info] Start training from

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:39: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.

C:\Users\Asus\AppData\Local\Temp\ipykernel_22380\400579187.py:40: FutureWarning:

Series.view is deprecated and will be removed in a future version. Use ``astype`` as an alternative to change the dtype.



[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Warning] Unknown parameter: enable_bindle
[LightGBM] [Warning] Unknown parameter: bososting_type
[LightGBM] [Warning] min_data_in_leaf is set=7, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=7
[LightGBM] [Info] Number of positive: 8378, number of negative: 749950
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.024006 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2003
[LightGBM] [Info] Number of data points in the train set: 758328, number of used features: 31
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.011048 -> initscore=-4.494397
[LightGBM] [Info] Start training from

KeyboardInterrupt: 